## Model buildiing
- Notebook used to validate feature selection for logistic regression 

In [315]:
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn import metrics
import pandas as pd
import pickle
import seaborn as sns
import numpy as np

#### Import dataset

In [9]:
df = pd.read_csv('../backend/mapping_heat/fixtures/pitching_data.csv')

In [10]:
df.dtypes.to_dict()

{'index': dtype('int64'),
 'pitch_type': dtype('O'),
 'game_date': dtype('O'),
 'release_speed': dtype('float64'),
 'release_pos_x': dtype('float64'),
 'release_pos_z': dtype('float64'),
 'player_name': dtype('O'),
 'batter': dtype('int64'),
 'pitcher': dtype('int64'),
 'events': dtype('O'),
 'description': dtype('O'),
 'spin_dir': dtype('float64'),
 'spin_rate_deprecated': dtype('float64'),
 'break_angle_deprecated': dtype('float64'),
 'break_length_deprecated': dtype('float64'),
 'zone': dtype('float64'),
 'des': dtype('O'),
 'game_type': dtype('O'),
 'stand': dtype('O'),
 'p_throws': dtype('O'),
 'home_team': dtype('O'),
 'away_team': dtype('O'),
 'type': dtype('O'),
 'hit_location': dtype('float64'),
 'bb_type': dtype('O'),
 'balls': dtype('int64'),
 'strikes': dtype('int64'),
 'game_year': dtype('int64'),
 'pfx_x': dtype('float64'),
 'pfx_z': dtype('float64'),
 'plate_x': dtype('float64'),
 'plate_z': dtype('float64'),
 'on_3b': dtype('float64'),
 'on_2b': dtype('float64'),
 'on_1

In [31]:
pd.set_option('display.max_columns', None)
df.head()

index pitch_type game_date  release_speed  release_pos_x  release_pos_z  \
0    613         FF   9/27/20           91.6           2.31           6.19   
1    635         SL   9/27/20           80.4           2.45           6.12   
2    637         SL   9/27/20           80.8           2.27           6.09   
3    660         SL   9/27/20           80.5           2.41           6.12   
4    661         SL   9/27/20           81.4           2.35           6.14   

  player_name  batter  pitcher     events      description  spin_dir  \
0   Brad Hand  605137   543272  field_out    hit_into_play       NaN   
1   Brad Hand  605137   543272        NaN             ball       NaN   
2   Brad Hand  592567   543272  strikeout  swinging_strike       NaN   
3   Brad Hand  592567   543272        NaN             foul       NaN   
4   Brad Hand  592567   543272        NaN  swinging_strike       NaN   

   spin_rate_deprecated  break_angle_deprecated  break_length_deprecated  \
0                   NaN                     NaN                      NaN   
1                   NaN                     NaN                      NaN   
2                   NaN                     NaN                      NaN   
3                   NaN                     NaN                      NaN   
4                   NaN                     NaN                      NaN   

   zone                                                des game_type stand  \
0   1.0  Josh Bell flies out to right fielder Jordan Lu...         R     R   
1  13.0                                                NaN         R     R   
2  13.0                Colin Moran strikes out swinging.           R     L   
3  13.0                                                NaN         R     L   
4  13.0                                                NaN         R     L   

  p_throws home_team away_team type  hit_location   bb_type  balls  strikes  \
0        L       CLE       PIT    X           9.0  fly_ball      1        0   
1        L       CLE       PIT    B           NaN       NaN      0        0   
2        L       CLE       PIT    S           2.0       NaN      0        2   
3        L       CLE       PIT    S           NaN       NaN      0        2   
4        L       CLE       PIT    S           NaN       NaN      0        1   

   game_year  pfx_x  pfx_z  plate_x  plate_z  on_3b  on_2b  on_1b  \
0       2020    0.9    1.3    -0.30     3.31    NaN    NaN    NaN   
1       2020   -1.1    0.0    -0.86     1.31    NaN    NaN    NaN   
2       2020   -1.4   -0.1    -1.90     1.26    NaN    NaN    NaN   
3       2020   -1.7    0.0    -0.90     1.80    NaN    NaN    NaN   
4       2020   -1.7    0.0    -0.98     2.25    NaN    NaN    NaN   

   outs_when_up  inning inning_topbot    hc_x    hc_y  tfs_deprecated  \
0             2       9           Top  217.94  101.96             NaN   
1             2       9           Top     NaN     NaN             NaN   
2             1       9           Top     NaN     NaN             NaN   
3             1       9           Top     NaN     NaN             NaN   
4             1       9           Top     NaN     NaN             NaN   

   tfs_zulu_deprecated  fielder_2  umpire  sv_id       vx0         vy0  \
0                  NaN     547379     NaN    NaN -8.326379 -133.205861   
1                  NaN     547379     NaN    NaN -5.260466 -116.999311   
2                  NaN     547379     NaN    NaN -6.545887 -117.560799   
3                  NaN     547379     NaN    NaN -4.073822 -117.239671   
4                  NaN     547379     NaN    NaN -4.216575 -118.535362   

        vz0         ax         ay         az  sz_top  sz_bot  hit_distance_sc  \
0 -4.261343  11.890496  25.776284 -15.718337    3.73    1.77            315.0   
1 -3.880876  -8.699110  21.709584 -31.961590    3.86    1.91              NaN   
2 -3.823399 -11.851736  21.561248 -33.038975    3.59    1.70              NaN   
3 -2.937641 -14.751489  23.216014 -31.542665    3.59    1.70              NaN

In [18]:
pitcheres = df.player_name.value_counts().to_frame().reset_index().rename(columns={'index': 'pitcher', 'player_name': 'count'})
pitcheres.head()

pitcher  count
0      Lance Lynn   1408
1    Shane Bieber   1238
2  German Marquez   1226
3   Lucas Giolito   1214
4    Max Scherzer   1213

In [19]:
pitcheres['count'].mean()

359.5961800818554

In [20]:
pitcheres['count'].min()

2

In [21]:
pitcheres['count'].describe()

count     733.000000
mean      359.596180
std       299.813281
min         2.000000
25%       118.000000
50%       302.000000
75%       470.000000
max      1408.000000
Name: count, dtype: float64

In [22]:
df.shape

(263584, 90)

In [23]:
df.player_name.value_counts().to_frame().mean()

player_name    359.59618
dtype: float64

In [24]:
df.release_speed.value_counts().head(10)

93.5    2154
93.9    2142
93.1    2142
93.3    2128
93.4    2123
93.8    2120
93.2    2113
94.1    2109
92.7    2100
92.9    2096
Name: release_speed, dtype: int64

In [25]:
rl_speed = df.release_speed.value_counts().to_frame().reset_index().rename(columns={'index': 'speed', 'release_speed': 'count'})

In [26]:
rl_speed.speed.describe()

count    466.000000
mean      77.944635
std       14.872838
min       38.100000
25%       67.125000
50%       78.750000
75%       90.375000
max      102.200000
Name: speed, dtype: float64

In [243]:
rl_speed.loc[rl_speed.speed.isnull()]

Empty DataFrame
Columns: [speed, count]
Index: []

In [27]:
df.type.value_counts()

S    121964
B     97648
X     43972
Name: type, dtype: int64

In [29]:
df.events.value_counts()

field_out                     25530
strikeout                     15543
single                         9071
walk                           5890
double                         2823
home_run                       2304
force_out                      1308
grounded_into_double_play      1235
hit_by_pitch                    821
field_error                     513
sac_fly                         399
triple                          241
double_play                     150
fielders_choice                 149
sac_bunt                        126
fielders_choice_out             118
caught_stealing_2b               71
strikeout_double_play            43
interf_def                       35
pickoff_caught_stealing_2b       14
pickoff_1b                       12
other_out                        11
pickoff_2b                        7
caught_stealing_3b                6
caught_stealing_home              4
sac_fly_double_play               3
run                               2
triple_play                 

In [33]:
def hot_encode_event(x):
    print(x)
    

In [35]:
# df['norm_event'] = df[~df.event.isin(['single', 'double', 'home_run', 'triple'])
df['norm_event'] = df['description'].apply(lambda x: hot_encode_event(x))

field_out
nan
strikeout
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
nan
walk
nan
nan
nan
nan
nan
field_out
nan
field_out
nan
field_out
nan
field_out
sac_fly
nan
nan
nan
nan
double
nan
nan
nan
nan
nan
double
nan
nan
nan
hit_by_pitch
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
single
single
nan
nan
nan
field_out
nan
nan
nan
field_out
home_run
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
double
nan
nan
field_out
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
double
nan
walk
nan
nan
nan
nan
double
nan
single
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
hit_by_pitch
nan
force_out
double
nan
nan
field_out
home_run
nan
double_play
nan
force_out
nan
nan
nan
nan
single
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
nan
nan
nan
home_run
nan
nan


nan
nan
nan
strikeout
nan
nan
nan
field_out
strikeout
nan
nan
force_out
nan
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
nan
walk
nan
nan
nan
nan
field_out
field_out
nan
nan
nan
nan
field_out
field_out
nan
nan
nan
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
walk
nan
nan
nan
nan
single
force_out
nan
nan
hit_by_pitch
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
hit_by_pitch
nan
nan
field_out
nan
nan
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
field_out
double
nan
nan
nan
walk
nan
nan
nan
nan
nan
double
nan
nan
strikeout
nan
nan
nan
nan
walk
nan
nan
nan
nan
home_run
nan
nan
nan
field_out
field_out
nan
nan
nan
field_out
nan
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
nan
single
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
nan
double
nan
nan
strikeout
nan
nan
nan
nan
fiel

nan
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
field_out
nan
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
field_out
home_run
nan
single
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
single
nan
nan
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
nan
nan
nan
walk
nan
nan
nan
nan
single
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
nan
home_run
nan
nan
field_out
single
nan
nan
nan
field_out
nan
nan
nan
nan
nan
double
strikeout
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
single
nan
nan
field_out
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
home_run
nan
nan
nan
nan
strikeout
nan
nan
nan
field_out
nan
nan
nan
double
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
single
nan
nan
nan
single
nan
nan
double
nan
nan
nan
nan
field_out
field_out


nan
single
nan
nan
strikeout
nan
nan
nan
nan
force_out
nan
nan
single
nan
nan
nan
nan
nan
home_run
home_run
nan
nan
nan
nan
nan
walk
nan
nan
nan
single
nan
nan
strikeout
nan
nan
nan
nan
nan
sac_fly
nan
sac_bunt
double
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
nan
single
nan
nan
nan
single
field_out
nan
single
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
single
strikeout
nan
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
field_out
field_out
field_out
single
nan
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
nan
walk
nan
nan
nan
single
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
nan
nan
field_out
strikeout
nan
nan
nan
nan
nan
other_out
nan
strikeout
nan
nan
nan
nan
nan
strikeout
nan
nan
walk
nan
nan
nan
nan
field_out
nan
nan
nan
fielders_choice_out
nan
nan
nan
nan
field_out
nan
single
nan
nan
nan
strikeout
nan
nan
nan
field_out
single
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
single

nan
nan
field_out
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
triple
nan
nan
nan
nan
walk
nan
nan
nan
field_out
nan
nan
nan
single
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
nan
nan
field_out
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
nan
double
nan
nan
nan
nan
field_out
nan
nan
nan
single
nan
field_out
field_out
nan
nan
walk
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
field_out
nan
nan
nan
nan
nan
nan
nan
nan
force_out
nan
nan
nan
single
nan
nan
walk
nan
nan
nan
nan
single
single
nan
nan
walk
nan
nan
nan
nan
nan
home_run
nan
field_out
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
double
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
hit_by_pitch
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan


...

nan
nan
nan
nan
nan
nan
caught_stealing_2b
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
force_out
single
nan
nan
strikeout
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
strikeout
nan
nan
nan
nan
nan
single
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
home_run
field_out
nan
nan
nan
nan
nan
nan
nan
field_out
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
field_out
nan
walk
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
sac_fly
nan
nan
nan
nan
single
single
nan
nan
nan
nan
field_out
nan
field_out
field_out
nan
nan
nan
field_out
nan
nan
nan
nan
nan
field_out
nan
field_out
nan
grounded_into_double_play
nan
nan
single
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
field_out
home_run
nan
nan
nan
single
nan
single
nan
nan
nan
nan
field_out
strikeout
nan
nan
nan
nan
nan
si

field_out
nan
home_run
field_out
nan
nan
field_out
nan
walk
nan
nan
nan
double
nan
strikeout
nan
nan
nan
single
nan
nan
nan
strikeout
nan
nan
strikeout
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
hit_by_pitch
nan
nan
nan
nan
nan
caught_stealing_2b
nan
walk
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
sac_fly
nan
nan
sac_bunt
strikeout
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
field_out
walk
nan
nan
nan
single
nan
field_out
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
field_out
single
nan
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
field_out
nan
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
field_out
nan
nan
nan
field_out
field_out
nan
field_out
field_out
field_out
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
strikeout
nan
nan
nan
field_out
nan
nan
nan
strikeout
nan
nan


nan
nan
strikeout
nan
nan
nan
field_out
nan
strikeout
nan
nan
nan
walk
nan
nan
nan
nan
walk
nan
nan
nan
nan
single
nan
nan
nan
nan
nan
field_out
field_out
nan
nan
walk
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
single
nan
nan
sac_bunt
double
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
nan
nan
nan
nan
nan
single
nan
strikeout
nan
nan
single
nan
field_out
nan
nan
field_out
nan
nan
nan
force_out
walk
nan
nan
nan
nan
nan
nan
strikeout
nan
nan
field_out
nan
nan
nan
single
nan
nan
nan
walk
nan
nan
nan
nan
single
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
nan
nan
nan
field_out
nan
single
nan
nan
nan
field_out
field_out
nan
field_out
nan
nan
walk
nan
nan
nan
nan
field_out
walk
nan
nan
nan
nan
nan
strikeout
nan
nan
strikeout
nan
nan
nan
fielders_choice
nan
nan
nan
nan
nan
nan
nan
single
nan
nan
nan
nan
nan
fielders_choice
nan
nan
walk
nan
nan
nan
nan
nan
nan
nan
field_out
nan
nan
nan
strikeout
nan
nan
nan
triple
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
field_out
nan

nan
nan
nan
nan
single
nan
strikeout
nan
nan
nan
nan
field_out
nan
sac_fly
nan
nan
field_out
nan
nan
nan
nan
field_error
nan
nan
nan
nan
grounded_into_double_play
field_out
walk
nan
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
nan
walk
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
single
nan
nan
nan
nan
nan
force_out
nan
force_out
strikeout
nan
nan
nan
nan
single
nan
nan
strikeout
nan
nan
nan
field_out
home_run
nan
nan
nan
nan
strikeout
nan
nan
single
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
nan
walk
nan
nan
nan
nan
walk
nan
nan
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
nan
field_out
nan
force_out
nan
nan
force_out
nan
nan
single
nan
field_out
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
nan
nan
field_out
nan
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
strikeout
n

nan
nan
nan
single
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
field_out
nan
nan
field_out
strikeout
nan
nan
nan
nan
walk
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
nan
strikeout
nan
nan
strikeout
nan
nan
nan
nan
field_out
nan
nan
nan
field_out
nan
nan
nan
nan
nan
strikeout
nan
nan
walk
nan
nan
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
grounded_into_double_play
nan
nan
nan
single
nan
nan
nan
field_out
home_run
nan
nan
nan
nan
field_out
nan
double
nan
nan
nan
nan
field_out
nan
nan
nan
nan
nan
field_out
nan
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
strikeout
nan
nan
nan
walk
nan
nan
nan
single
nan
nan
nan
walk
nan
nan
nan
nan
nan
walk
nan
nan
nan
nan
nan
nan
single
nan
fielders_choice_out
fielders_choice
nan
double
nan
single
nan
nan
nan
field_out
field_out
field_out
strikeout
nan
nan
nan
nan
nan
force_out
single
nan
field_out
nan
nan
nan
field_out
nan
nan
field_out
nan
nan
strikeout
nan
nan
nan
nan
nan
field_out
nan
nan
nan
nan
st

In [32]:
df.description.value_counts()

ball                       89937
foul                       44716
called_strike              44320
hit_into_play              28264
swinging_strike            28026
hit_into_play_no_out        9685
blocked_ball                6874
hit_into_play_score         6029
foul_tip                    2427
swinging_strike_blocked     1968
hit_by_pitch                 821
foul_bunt                    434
missed_bunt                   62
pitchout                      16
bunt_foul_tip                  5
Name: description, dtype: int64

In [37]:
df_features = df[['description', 'events', 'type', 'release_speed', ]]

In [38]:
encoded = pd.get_dummies(df_features)

In [39]:
encoded.head()

release_speed  description_ball  description_blocked_ball  \
0           91.6                 0                         0   
1           80.4                 1                         0   
2           80.8                 0                         0   
3           80.5                 0                         0   
4           81.4                 0                         0   

   description_bunt_foul_tip  description_called_strike  description_foul  \
0                          0                          0                 0   
1                          0                          0                 0   
2                          0                          0                 0   
3                          0                          0                 1   
4                          0                          0                 0   

   description_foul_bunt  description_foul_tip  description_hit_by_pitch  \
0                      0                     0                         0   
1                      0                     0                         0   
2                      0                     0                         0   
3                      0                     0                         0   
4                      0                     0                         0   

   description_hit_into_play  description_hit_into_play_no_out  \
0                          1                                 0   
1                          0                                 0   
2                          0                                 0   
3                          0                                 0   
4                          0                                 0   

   description_hit_into_play_score  description_missed_bunt  \
0                                0                        0   
1                                0                        0   
2                                0                        0   
3                                0                        0   
4                                0                        0   

   description_pitchout  description_swinging_strike  \
0                     0                            0   
1                     0                            0   
2                     0                            1   
3                     0                            0   
4                     0                            1   

   description_swinging_strike_blocked  events_caught_stealing_2b  \
0                                    0                          0   
1                                    0                          0   
2                                    0                          0   
3                                    0                          0   
4                                    0                          0   

   events_caught_stealing_3b  events_caught_stealing_home  events_double  \
0                          0                            0              0   
1                          0                            0              0   
2                          0                            0              0   
3                          0                            0              0   
4                          0                            0              0   

   events_double_play  events_field_error  events_field_out  \
0                   0                   0                 1   
1                   0                   0                 0   
2                   0                   0                 0   
3                   0                   0                 0   
4                   0                   0                 0   

   events_fielders_choice  events_fielders_choice_out  events_force_out  \
0                       0                           0                 0   
1                       0                           0                 0   
2                       0                           0                 0   
3                       0         

In [40]:
df.zone

0          1.0
1         13.0
2         13.0
3         13.0
4         13.0
          ... 
263579     5.0
263580     7.0
263581     9.0
263582    11.0
263583    11.0
Name: zone, Length: 263584, dtype: float64

In [245]:
df[df.zone.isnull()][['description']]

description
20677            ball
20682            ball
70022   hit_into_play
70023    blocked_ball
70024   called_strike
...               ...
233601           foul
233738           foul
234935           ball
234937           ball
261997   blocked_ball

[191 rows x 1 columns]

- AB Automatic Ball
- AS Automatic Strike
- CH Change-​up
- CU Curveball
- EP Eephus
- FC Cutter
- FF Four-Seam Fastball
- FO Forkball
- FS Splitter
- FT Two-Seam Fastball (synonymous with SI)
- GY Gyroball
- IN Intentional Ball
- KC Knuckle Curve
- KN Knuckleball
- NP No Pitch
- PO Pitchout
- SC Screwball
- SI Sinker (synonymous with FT)
- SL Slider
- UN Unknown

In [41]:
df.pitch_type.value_counts()

FF    89618
SL    46849
SI    42768
CH    31131
CU    24679
FC    17404
KC     5939
FS     4528
CS      191
KN       23
FO        3
Name: pitch_type, dtype: int64

In [291]:
x = df[~df.zone.isnull()].copy()

In [292]:
x.shape

(263393, 91)

In [293]:
x.columns

Index(['index', 'pitch_type', 'game_date', 'release_speed', 'release_pos_x',
       'release_pos_z', 'player_name', 'batter', 'pitcher', 'events',
       'description', 'spin_dir', 'spin_rate_deprecated',
       'break_angle_deprecated', 'break_length_deprecated', 'zone', 'des',
       'game_type', 'stand', 'p_throws', 'home_team', 'away_team', 'type',
       'hit_location', 'bb_type', 'balls', 'strikes', 'game_year', 'pfx_x',
       'pfx_z', 'plate_x', 'plate_z', 'on_3b', 'on_2b', 'on_1b',
       'outs_when_up', 'inning', 'inning_topbot', 'hc_x', 'hc_y',
       'tfs_deprecated', 'tfs_zulu_deprecated', 'fielder_2', 'umpire', 'sv_id',
       'vx0', 'vy0', 'vz0', 'ax', 'ay', 'az', 'sz_top', 'sz_bot',
       'hit_distance_sc', 'launch_speed', 'launch_angle', 'effective_speed',
       'release_spin_rate', 'release_extension', 'game_pk', 'pitcher.1',
       'fielder_2.1', 'fielder_3', 'fielder_4', 'fielder_5', 'fielder_6',
       'fielder_7', 'fielder_8', 'fielder_9', 'release_pos_y',
     

In [294]:
def hot_encode_des(x):
    if x == 'hit_into_play_no_out' or x == 'hit_into_play_score':
        return 1
    return 0
    

In [296]:
x_norm = x[['player_name', 'pitch_type', 'release_speed', 'zone']]

In [297]:
y = x['description'].apply(lambda x: hot_encode_des(x))

In [298]:
x = pd.get_dummies(x_norm[['player_name', 'pitch_type', 'release_speed', 'zone']])

In [299]:
y

0         0
1         0
2         0
3         0
4         0
         ..
263579    0
263580    0
263581    0
263582    0
263583    0
Name: description, Length: 263393, dtype: int64

In [300]:
X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.30)

In [302]:
X_train

release_speed  zone  player_name_A.J. Cole  player_name_A.J. Minter  \
54656            93.2  14.0                      0                        0   
47074            84.0   8.0                      0                        0   
69375            92.6  11.0                      0                        0   
111745           82.9  13.0                      0                        0   
131469           93.2   7.0                      0                        0   
...               ...   ...                    ...                      ...   
158437           85.2  11.0                      0                        0   
9697             90.2  12.0                      0                        0   
32743            85.7  11.0                      0                        0   
193882           80.9   9.0                      0                        0   
52464            80.0  13.0                      0                        0   

        player_name_AJ Ramos  player_name_Aaron Barrett  \
54656                      0                          0   
47074                      0                          0   
69375                      0                          0   
111745                     0                          0   
131469                     0                          0   
...                      ...                        ...   
158437                     0                          0   
9697                       0                          0   
32743                      0                          0   
193882                     0                          0   
52464                      0                          0   

        player_name_Aaron Bummer  player_name_Aaron Civale  \
54656                          0                         0   
47074                          0                         0   
69375                          0                         0   
111745                         0                         0   
131469                         0                         0   
...                          ...                       ...   
158437                         0                         0   
9697                           0                         0   
32743                          0                         0   
193882                         0                         0   
52464                          0                         0   

        player_name_Aaron Fletcher  player_name_Aaron Loup  \
54656                            0                       0   
47074                            0                       0   
69375                            0                       0   
111745                           0                       0   
131469                           0                       0   
...                            ...                     ...   
158437                           0                       0   
9697                             0                       0   
32743                            0                       0   
193882                           0                       0   
52464                            0                       0   

        player_name_Aaron Nola  player_name_Aaron Slegers  \
54656                        0                          0   
47074                        0                          0   
69375                        0                          0   
111745                       0                          0   
131469                       0                          0   
...                        ...                        ...   
158437                       0                          0   
9697                         0                          0   
32743                        0                          0   
193882                       0                          0   
52464                        0                          0   

        player_name_Adam Cimber  player_name_Adam Kolarek  \
54656                         0                         0   
47074

#### Build probability model

In [303]:
clf = LogisticRegression(max_iter=500)

In [304]:
clf.fit(X_train, y_train)

/usr/local/lib/python3.8/site-packages/sklearn/linear_model/_logistic.py:938: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=500,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=None, solver='lbfgs', tol=0.0001, verbose=0,
                   warm_start=False)

In [305]:
pred = clf.predict(X_test)

In [306]:
pred

array([0, 0, 0, ..., 0, 0, 0])

In [307]:
score = metrics.accuracy_score(y_test, pred)

In [308]:
score

0.9399124250170847

In [314]:
clf.predict_proba(X=X_test)

array([[0.97768113, 0.02231887],
       [0.9658379 , 0.0341621 ],
       [0.93568287, 0.06431713],
       ...,
       [0.95869814, 0.04130186],
       [0.97067599, 0.02932401],
       [0.97098172, 0.02901828]])

In [316]:
# save the model to disk
filename = 'pitch_prob.sav'
pickle.dump(clf, open(filename, 'wb'))